In [1]:
# Load Packages
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import plotly.express as px

import warnings

warnings.filterwarnings("ignore")

from typing import List

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.preprocessing import MinMaxScaler

import keras

import sys, os
rootpath = ".."
sys.path.insert(0, f"{os.getcwd()}/{rootpath}/models")
import model_prep

step_back = 6  # window size = 6*5 = 30 mins
season_map = {
    "spring": [3, 4, 5],
    "summer": [6, 7, 8],
    "fall": [9, 10, 11],
    "winter": [12, 1, 2],
}

2023-07-26 22:48:58.520673: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
# building_name = "Kissam"
# tower_number = 1
# features = ['Kissam_Tower_1 enteringWaterTemp', 'Kissam_Tower_1 outdoorAirDryBulb', 'Kissam_Tower_1 outdoorAirWetBulb', 'Kissam_Tower_1 vfdPercent', 'Kissam_Tower_1 fanA_vfdPower', 'Kissam_Tower_1 fanB_vfdPower', 'Kissam_Tower_1 dayOfWeek', 'Kissam_Tower_1 hourOfDay']
# target = "Kissam_Tower_1 leavingWaterTemp"
# season = "summer"
# use_delta = True
# train_percentage = 0.75
# shuffle_seed = 42

In [3]:
from_building_name = "Kissam"
from_tower_number = 1
from_target = "Kissam_Tower_1 leavingWaterTemp"
from_features = ['Kissam_Tower_1 enteringWaterTemp', 'Kissam_Tower_1 outdoorAirDryBulb', 'Kissam_Tower_1 outdoorAirWetBulb', 'Kissam_Tower_1 vfdPercent', 'Kissam_Tower_1 fanA_vfdPower', 'Kissam_Tower_1 fanB_vfdPower', 'Kissam_Tower_1 dayOfWeek', 'Kissam_Tower_1 hourOfDay']
to_building_name = "ESB"
to_tower_number = 1
to_features = ['ESB_Tower_1 enteringWaterTemp', 'ESB_Tower_1 outdoorAirDryBulb', 'ESB_Tower_1 outdoorAirWetBulb', 'ESB_Tower_1 vfdPercent', 'ESB_Tower_1 fanA_vfdPower', 'ESB_Tower_1 fanB_vfdPower', 'ESB_Tower_1 dayOfWeek', 'ESB_Tower_1 hourOfDay']
to_target = "ESB_Tower_1 leavingWaterTemp"
to_season = "summer"
from_season = "summer"
train_percentage = 0.75
target_domain_percentage = 0.2
display_results = True
use_delta = True
shuffle_seed = 42
finetune_epochs = 10

In [4]:
"""
1. Convert data into a model-compatible shape
"""

lstm_df, first_temp = model_prep.create_preprocessed_lstm_df(
    building_name=from_building_name,
    tower_number=from_tower_number,
    features=from_features,
    target=from_target,
    season=from_season,
    use_delta=use_delta,
)
if not from_season:
    from_season = "allyear"

"""
2. Split data into training and testing sets
"""

X = lstm_df.drop(f"{from_target}(t)", axis=1)  # drop target column
y = lstm_df[f"{from_target}(t)"]  # only have target column

# split into input and outputs
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=(1 - train_percentage), shuffle=True, random_state=shuffle_seed
)

# scale feature data
scaler = MinMaxScaler().fit(X_train)
X_train[X_train.columns] = scaler.transform(X_train)
X_test[X_test.columns] = scaler.transform(X_test)

"""
3. Get timestepped data as a 3D vector
"""
vec_X_train = model_prep.df_to_3d(
    lstm_dtframe=X_train, num_columns=len(from_features) + 1, step_back=step_back
)
vec_X_test = model_prep.df_to_3d(
    lstm_dtframe=X_test, num_columns=len(from_features) + 1, step_back=step_back
)

vec_y_train = y_train.values
vec_y_test = y_test.values

In [5]:
# from keras.models import Sequential
# from keras.layers import LSTM, Dense

# # Define the number of features in the input data
# num_features = len(features) + 1

# # Define the number of timesteps to use as input
# timesteps = 6

# # Define the number of neurons in the encoder and LSTM layers
# latent_dim = 32

# # Create the model
# model = Sequential()
# model.add(Dense(latent_dim, activation='relu', input_shape=(timesteps, num_features))) # encoder
# model.add(LSTM(latent_dim)) # lstm
# model.add(Dense(1)) # decoder

# # Compile the model
# model.compile(optimizer='adam', loss='mse')
# model.summary()

In [6]:
from keras.models import Model
from keras.layers import Input, Dense, LSTM

# Define input shape for the autoencoder
timesteps = step_back
input_dim = len(from_features) + 1
input_shape = (timesteps, input_dim)

# Define the autoencoder architecture
inputs = Input(shape=input_shape)

# Dense encoder layer
encoder = Dense(units=64, activation='relu')(inputs)

# LSTM bottleneck layer
lstm_layer = LSTM(units=32, activation='relu')(encoder)

# Dense decoder layer
decoder = Dense(units=64, activation='relu')(lstm_layer)

# Output layer to predict the next timestep
output = Dense(units=1)(decoder)

# Create the autoencoder model
model = Model(inputs=inputs, outputs=output)

# Compile the autoencoder model
model.compile(optimizer='adam', loss='mse')

# Print the summary of the autoencoder model
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 6, 9)]            0         
                                                                 
 dense (Dense)               (None, 6, 64)             640       
                                                                 
 lstm (LSTM)                 (None, 32)                12416     
                                                                 
 dense_1 (Dense)             (None, 64)                2112      
                                                                 
 dense_2 (Dense)             (None, 1)                 65        
                                                                 
Total params: 15,233
Trainable params: 15,233
Non-trainable params: 0
_________________________________________________________________


2023-07-26 22:49:03.595482: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [7]:
history = model.fit(
    vec_X_train,
    vec_y_train,
    epochs=50,
    batch_size=72,
    validation_data=(vec_X_test, vec_y_test),
    verbose=0,
    shuffle=False,
)

In [8]:
# make predictions
yhat = model.predict(vec_X_test)

201/201 [==============================] - 0s 962us/step


In [9]:
"""
5. Display results
"""
results_df = pd.DataFrame(
    {
        "actual": vec_y_test.reshape((vec_y_test.shape[0])),
        "predicted": yhat.reshape((yhat.shape[0])),
    },
    index=y_test.index,
)

if use_delta:
    results_df["actual"] = results_df["actual"] + first_temp
    results_df["predicted"] = results_df["predicted"] + first_temp

# SAVE ERROR AND DATA AVAILABILITY INFORMATION

# calculate, display and save error results
mae = mean_absolute_error(results_df["actual"], results_df["predicted"])
rmse = np.sqrt(mean_squared_error(results_df["actual"], results_df["predicted"]))
mae_sd = np.std(np.abs(results_df["actual"] - results_df["predicted"]))

# GENERATE PLOTS

# Create a new DataFrame with the desired 5-minute interval index, and merge the new DataFrame with the original DataFrame
display_df = pd.DataFrame(
    index=pd.date_range(
        start=results_df.index.min(), end=results_df.index.max(), freq="5min"
    )
).merge(results_df, how="left", left_index=True, right_index=True)

# display trend of temperature predictions (actual vs predicted)
fig = px.line(display_df, x=display_df.index, y=["actual", "predicted"])
fig.update_layout(
    title=f"{from_building_name} Tower {from_tower_number} Autoencoder LSTM Model Results",
    xaxis_title="time",
    yaxis_title=from_target,
)
fig.show()

# save the model
print(model.summary())

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 6, 9)]            0         
                                                                 
 dense (Dense)               (None, 6, 64)             640       
                                                                 
 lstm (LSTM)                 (None, 32)                12416     
                                                                 
 dense_1 (Dense)             (None, 64)                2112      
                                                                 
 dense_2 (Dense)             (None, 1)                 65        
                                                                 
Total params: 15,233
Trainable params: 15,233
Non-trainable params: 0
_________________________________________________________________
None


## Transfer

In [10]:
"""
1. Load data and do LSTM preprocessing
"""

lstm_to_df, to_first_temp = model_prep.create_preprocessed_lstm_df(
    building_name=to_building_name,
    tower_number=to_tower_number,
    features=to_features,
    target=to_target,
    season=to_season,
    use_delta=use_delta,
)
if not to_season:
    to_season = from_season = "allyear"

In [11]:
"""
2. Convert tower data into a model-compatible shape i.e. get timestepped data as a 3D vector
"""

X = lstm_to_df.drop(f"{to_target}(t)", axis=1)  # drop target column
y = lstm_to_df[f"{to_target}(t)"]  # only have target column

# split train and test set
X_train, X_test, y_train, y_test = train_test_split(
    X,
    y,
    test_size=(1 - target_domain_percentage),
    shuffle=False,
    random_state=shuffle_seed,
)

# scale feature data
scaler = MinMaxScaler()
scaler = scaler.fit(X_train)
X_train[X_train.columns] = scaler.transform(X_train)
X_test[X_test.columns] = scaler.transform(X_test)

# create 3d vector form of data
vec_X_train = model_prep.df_to_3d(
    lstm_dtframe=X_train,
    num_columns=len(to_features) + 1,
    step_back=step_back,
)
vec_X_test = model_prep.df_to_3d(
    lstm_dtframe=X_test,
    num_columns=len(to_features) + 1,
    step_back=step_back,
)

vec_y_train = y_train.values
vec_y_test = y_test.values

In [12]:
model.layers

In [13]:
# finetune model

# freeze encoder and decoder layers
model.layers[1].trainable = False
model.layers[3].trainable = False
model.layers[4].trainable = False
# keep lstm layer finetuneable
model.layers[0].trainable = True
model.layers[2].trainable = True

model.compile(
    optimizer=keras.optimizers.Adam(1e-5),  # Very low learning rate
    loss="mse",
    metrics=[keras.metrics.BinaryAccuracy()],
)

history = model.fit(
    vec_X_train,
    vec_y_train,
    epochs=finetune_epochs,
    verbose=0,
    shuffle=False,
)

In [14]:
# make predictions
yhat = model.predict(vec_X_test)

359/359 [==============================] - 0s 923us/step


In [15]:
"""
5. Display results
"""
results_df = pd.DataFrame(
    {
        "actual": vec_y_test.reshape((vec_y_test.shape[0])),
        "predicted": yhat.reshape((yhat.shape[0])),
    },
    index=y_test.index,
)

if use_delta:
    results_df["actual"] = results_df["actual"] + first_temp
    results_df["predicted"] = results_df["predicted"] + first_temp

# SAVE ERROR AND DATA AVAILABILITY INFORMATION

# calculate, display and save error results
mae = mean_absolute_error(results_df["actual"], results_df["predicted"])
rmse = np.sqrt(mean_squared_error(results_df["actual"], results_df["predicted"]))
mae_sd = np.std(np.abs(results_df["actual"] - results_df["predicted"]))

# GENERATE PLOTS

# Create a new DataFrame with the desired 5-minute interval index, and merge the new DataFrame with the original DataFrame
display_df = pd.DataFrame(
    index=pd.date_range(
        start=results_df.index.min(), end=results_df.index.max(), freq="5min"
    )
).merge(results_df, how="left", left_index=True, right_index=True)

# display trend of temperature predictions (actual vs predicted)
fig = px.line(display_df, x=display_df.index, y=["actual", "predicted"])
fig.update_layout(
    title=f"{from_building_name} Tower {from_tower_number} Autoencoder LSTM Model Results",
    xaxis_title="time",
    yaxis_title=from_target,
)
fig.show()

# save the model
print(model.summary())

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 6, 9)]            0         
                                                                 
 dense (Dense)               (None, 6, 64)             640       
                                                                 
 lstm (LSTM)                 (None, 32)                12416     
                                                                 
 dense_1 (Dense)             (None, 64)                2112      
                                                                 
 dense_2 (Dense)             (None, 1)                 65        
                                                                 
Total params: 15,233
Trainable params: 12,416
Non-trainable params: 2,817
_________________________________________________________________
None
